<a href="https://www.kaggle.com/code/nurielreuven/blackjacks-hands-win-prediction-86-percision?scriptVersionId=96377360" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

By Nuriel Reuven

Version 1.0 , Uploaded on 10.5.22  |  2022- ©All Rights Reserved

# Background

![](https://upload.wikimedia.org/wikipedia/commons/4/4b/Blackjack_board.JPG)

Blackjack is a known casino game. The game is played between a player (or several players) and a dealer. The goal of the game is to have the highest sum of cards,but not exceeding 21. If the player's sum of cards is higher than the dealer's (and not exceeding 21), the player wins, And vice versa. Once the sum of the cards exceeds 21, the cards holder is busted.

Statistically the odds are not in the player's favor, since he is the first to play. This makes it a popular casino game. Several methods to tilt the odds to the player's favor have been developed (and proved mathematically), however in this notebook we will not use them and try to analyze a set of hands, extract statistics and try to develope a model to predict wether the player can win/lose/push (tie) in a round.

You do not need to know more than the basic rules of the game to understand this notebook. If you'd still wish to read more about the rules of the game, click [here](https://en.wikipedia.org/wiki/Blackjack#Rules_of_play_at_casinos) or [here ](https://www.youtube.com/watch?v=qd5oc9hLrXg&t=48s&ab_channel=Howcast)


The dataset contains simulation of 50M hands of blackjack with some exceptions to the rules. To read about the dataset,generator and exceptions click [here ](https://www.kaggle.com/datasets/dennisho/blackjack-hands)

# Data Exploration

In [1]:
import pandas as pd
import numpy as np
import plotly_express as px
import ipywidgets as widgets
import ast
from math import nan
import warnings
warnings.filterwarnings('ignore')

We will use only 250000 samples as 50M requires way too much computational resources :)

In [2]:
data = pd.read_csv('../input/blackjack-hands/blackjack_simulator.csv', sep = ',' , nrows = 250000)  # Because 5M is too much :)
data.head(10)

shoe_id  cards_remaining  dealer_up initial_hand   dealer_final  \
0        0              416         10     [10, 11]    [10, 4, 10]   
1        0              411         10       [5, 5]        [10, 8]   
2        0              406          6      [3, 10]     [6, 6, 10]   
3        0              401         10       [5, 9]        [10, 8]   
4        0              395          8      [6, 10]     [8, 2, 10]   
5        0              389          7       [3, 4]     [7, 2, 10]   
6        0              383          6       [3, 3]    [6, 10, 10]   
7        0              374          3      [10, 8]     [3, 10, 7]   
8        0              369          5      [8, 10]     [5, 10, 9]   
9        0              364          9       [6, 8]  [9, 2, 5, 11]   

  dealer_final_value             player_final player_final_value  \
0                 24               [[10, 11]]             ['BJ']   
1                 18             [[5, 5, 11]]               [21]   
2                 22                [[3, 10]]               [13]   
3                 18          [[5, 9, 11, 3]]               [18]   
4                 20            [[6, 10, 10]]               [26]   
5                 19             [[3, 4, 11]]               [18]   
6                 26  [[3, 2, 10], [3, 4, 5]]           [15, 12]   
7                 20                [[10, 8]]               [18]   
8                 24                [[8, 10]]               [18]   
9                 17              [[6, 8, 6]]               [20]   

                   actions_taken  run_count  true_count  win  
0                        [['S']]          1           0  1.5  
1                   [['H', 'S']]         -2           0  1.0  
2                        [['S']]         -2           0  1.0  
3              [['H', 'H', 'S']]         -1           0  0.0  
4                        [['H']]         -1           0 -1.0  
5                   [['H', 'S']]         -2           0 -1.0  
6  [['P', 'H', 'S'], ['H', 'S']]         -1           0  2.0  
7                        [['S']]          2           0 -1.0  
8                        [['S']]          1           0  1.0  
9                   [['H', 'S']]          0           0  1.0

**Reminder:** S = Stand , H = Hit , D = Double , P = Split , R = Surrender , I = Insurance , N = No Insurance

*shoe_id* is not relevant for neither the analysis or model building, so we will remove it.*run_count* and *true_count* are used for [cards counting](https://en.wikipedia.org/wiki/Card_counting). We will not discuss it in the analysis, although it will be used for model building.

We can already see that when a player is splitting cards it does not mention the split in all hands in action taken (i.e index 6, the 2nd hand actions are  ['H', 'S'] and not  ['P','H','S']). We will correct that later.

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250000 entries, 0 to 249999
Data columns (total 12 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   shoe_id             250000 non-null  int64  
 1   cards_remaining     250000 non-null  int64  
 2   dealer_up           250000 non-null  int64  
 3   initial_hand        250000 non-null  object 
 4   dealer_final        250000 non-null  object 
 5   dealer_final_value  250000 non-null  object 
 6   player_final        250000 non-null  object 
 7   player_final_value  250000 non-null  object 
 8   actions_taken       250000 non-null  object 
 9   run_count           250000 non-null  int64  
 10  true_count          250000 non-null  int64  
 11  win                 250000 non-null  float64
dtypes: float64(1), int64(5), object(6)
memory usage: 22.9+ MB


No Null objects found!

In [4]:
type(data['initial_hand'][1]) , type(data['dealer_final'][1])

(str, str)

We can see that the lists in our dataset are as string representation of list and not actual list, so we will convert all those columns to lists

In [5]:
data['initial_hand'] = data['initial_hand'].apply(lambda x: ast.literal_eval(x))
data['dealer_final'] = data['dealer_final'].apply(lambda x: ast.literal_eval(x))
data['player_final'] = data['player_final'].apply(lambda x: ast.literal_eval(x))
data['player_final_value'] = data['player_final_value'].apply(lambda x: ast.literal_eval(x))	
data['actions_taken'] = data['actions_taken'].apply(lambda x: ast.literal_eval(x))	

Now after converting to list we are able to correct the split bug that was mentioned before, we will use for loop tho its not convinient

In [6]:
data['actions_taken'] = data['actions_taken'].apply(lambda x: [x[0] , ['P'] + x[1]]  if len(x)==2 else x).apply(lambda x: [x[0] , ['P'] + x[1], ['P'] + x[2]]  if len(x)==3 else x).apply(lambda x: [x[0] , ['P'] + x[1], ['P'] + x[2], ['P'] + x[3]]  if len(x)==4 else x).apply(lambda x: [x[0] , ['P'] + x[1], ['P'] + x[2], ['P'] + x[3] , ['P'] + x[4]]  if len(x)==5 else x)

In [7]:
data.iloc[6]

shoe_id                                     0
cards_remaining                           383
dealer_up                                   6
initial_hand                           [3, 3]
dealer_final                      [6, 10, 10]
dealer_final_value                         26
player_final          [[3, 2, 10], [3, 4, 5]]
player_final_value                   [15, 12]
actions_taken          [[P, H, S], [P, H, S]]
run_count                                  -1
true_count                                  0
win                                       2.0
Name: 6, dtype: object

The bug was fixed

As we saw before,some lines have several hands info in 1 line (due to split, for example , like line 6 from before). We would like to do is to split to one hand per row. This would be easy using pandas .explode()

In [8]:
data = data.explode(['player_final','player_final_value','actions_taken'])

In [9]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 257004 entries, 0 to 249999
Data columns (total 12 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   shoe_id             257004 non-null  int64  
 1   cards_remaining     257004 non-null  int64  
 2   dealer_up           257004 non-null  int64  
 3   initial_hand        257004 non-null  object 
 4   dealer_final        257004 non-null  object 
 5   dealer_final_value  257004 non-null  object 
 6   player_final        257004 non-null  object 
 7   player_final_value  257004 non-null  object 
 8   actions_taken       257004 non-null  object 
 9   run_count           257004 non-null  int64  
 10  true_count          257004 non-null  int64  
 11  win                 257004 non-null  float64
dtypes: float64(1), int64(5), object(6)
memory usage: 25.5+ MB


7004 lines were added.
We would like to split the lists of player's and dealer's cards and players actions for future calculations. We will create a function to split them and apply it

In [10]:
def cards_splitter(data,cards,text):
    stopsign = cards.apply(lambda x: len(x))
    for i in range(1,max(stopsign)):
        data[f'{text}{i}'] = cards.apply(lambda x: nan if len(x)<i else x[i-1])


In [11]:
cards_splitter(data,data['player_final'],'player_card_')
cards_splitter(data,data['dealer_final'],'dealer_card_')
cards_splitter(data,data['actions_taken'],'action_taken_')

In [12]:
data.sample(5)

shoe_id  cards_remaining  dealer_up initial_hand   dealer_final  \
65690      1080              217         11      [7, 10]  [11, 3, 9, 7]   
169225     2784              358          6      [10, 3]     [6, 10, 6]   
76079      1251              158          8      [10, 2]        [8, 10]   
182337     3000              371          8       [9, 6]         [8, 9]   
48449       796              139         10      [6, 10]    [10, 4, 10]   

       dealer_final_value player_final player_final_value actions_taken  \
65690                  20      [7, 10]                 17        [N, R]   
169225                 22      [10, 3]                 13           [S]   
76079                  18  [10, 2, 10]                 22           [H]   
182337                 17   [9, 6, 10]                 25           [H]   
48449                  24      [6, 10]                 16           [R]   

        run_count  ...  dealer_card_4  dealer_card_5  dealer_card_6  \
65690          10  ...            7.0            NaN            NaN   
169225          5  ...            NaN            NaN            NaN   
76079          -5  ...            NaN            NaN            NaN   
182337         -5  ...            NaN            NaN            NaN   
48449           8  ...            NaN            NaN            NaN   

        dealer_card_7  action_taken_1  action_taken_2  action_taken_3  \
65690             NaN               N               R             NaN   
169225            NaN               S             NaN             NaN   
76079             NaN               H             NaN             NaN   
182337            NaN               H             NaN             NaN   
48449             NaN               R             NaN             NaN   

        action_taken_4  action_taken_5  action_taken_6  
65690              NaN             NaN             NaN  
169225             NaN             NaN             NaN  
76079              NaN             NaN             NaN  
182337             NaN             NaN             NaN  
48449              NaN             NaN             NaN  

[5 rows x 32 columns]

In [13]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 257004 entries, 0 to 249999
Data columns (total 32 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   shoe_id             257004 non-null  int64  
 1   cards_remaining     257004 non-null  int64  
 2   dealer_up           257004 non-null  int64  
 3   initial_hand        257004 non-null  object 
 4   dealer_final        257004 non-null  object 
 5   dealer_final_value  257004 non-null  object 
 6   player_final        257004 non-null  object 
 7   player_final_value  257004 non-null  object 
 8   actions_taken       257004 non-null  object 
 9   run_count           257004 non-null  int64  
 10  true_count          257004 non-null  int64  
 11  win                 257004 non-null  float64
 12  player_card_1       257004 non-null  int64  
 13  player_card_2       257004 non-null  int64  
 14  player_card_3       115671 non-null  float64
 15  player_card_4       31174 non-null

Another thing we'd like to do is to replace 'BJ' to 21 to stay in int types only. To differ wether the hand was blackjack or just a sum of 21 we will add 2 new columns of 'is_blackjack_player' and 'is_blackjack_dealer'. 

In [14]:
data['is_blackjack_dealer'] = data['dealer_final_value'].where(data['dealer_final_value'] == 'BJ').fillna(0).replace('BJ',1)
data['is_blackjack_player'] = data['player_final_value'].where(data['player_final_value'] == 'BJ').fillna(0).replace('BJ',1)

In [15]:
data['dealer_final_value'] = data['dealer_final_value'].replace('BJ',21)
data['player_final_value'] = data['player_final_value'].replace('BJ',21)

In [16]:
type(data['player_final_value'][0]) , type(data['dealer_final_value'][0])

(numpy.int64, str)

We can see the player_final_value and dealer_final_value are represented as string instead of int, we will correct that:

In [17]:
data['dealer_final_value'] = data['dealer_final_value'].astype('int64')
data['player_final_value'] = data['player_final_value'].astype('int64')

In [18]:
type(data['player_final_value'][0]) , type(data['dealer_final_value'][0])

(numpy.int64, numpy.int64)

Last thing we need to do is to correct the win amount as it is normalized to the cases where each row contained several hands. It would be easy as we have all data about the cards and the rules of the game. We will not use the win amount but mark a pure Win/Loss/Push case.

In [19]:
data.loc[(data['dealer_final_value'] < data['player_final_value']) & (data['player_final_value'] <= 21) , 'win'] = 1
data.loc[data['dealer_final_value'] >  21 , 'win'] = 1
data.loc[data['dealer_final_value'] == data['player_final_value'], 'win'] = 0
data.loc[(data['dealer_final_value'] > data['player_final_value']) & (data['dealer_final_value'] <= 21) , 'win'] = -1
data.loc[data['player_final_value'] > 21 , 'win'] = -1
data['win'] = data['win'].astype('int64')

 Win = 1 , Push = 0 , Loss = -1

To check our classification was correct:

In [20]:
data['win']

0         1
1         1
2         1
3         0
4        -1
         ..
249995   -1
249996   -1
249997    1
249998   -1
249999   -1
Name: win, Length: 257004, dtype: int64

In [21]:
data.sample(5)

shoe_id  cards_remaining  dealer_up initial_hand dealer_final  \
236016     3883              283          4       [9, 7]   [4, 3, 11]   
105365     1733              299          7      [3, 10]      [7, 10]   
89383      1470              222         10       [2, 4]   [10, 2, 5]   
145073     2387              354         10     [10, 10]     [10, 10]   
207067     3406              224         11      [3, 10]  [11, 6, 10]   

        dealer_final_value   player_final  player_final_value actions_taken  \
236016                  18         [9, 7]                  16           [S]   
105365                  17    [3, 10, 10]                  23           [H]   
89383                   17  [2, 4, 10, 8]                  24        [H, H]   
145073                  20       [10, 10]                  20           [S]   
207067                  17     [3, 10, 4]                  17     [N, H, S]   

        run_count  ...  dealer_card_6  dealer_card_7  action_taken_1  \
236016          0  ...            NaN            NaN               S   
105365          3  ...            NaN            NaN               H   
89383          -9  ...            NaN            NaN               H   
145073          8  ...            NaN            NaN               S   
207067          4  ...            NaN            NaN               N   

        action_taken_2  action_taken_3  action_taken_4  action_taken_5  \
236016             NaN             NaN             NaN             NaN   
105365             NaN             NaN             NaN             NaN   
89383                H             NaN             NaN             NaN   
145073             NaN             NaN             NaN             NaN   
207067               H               S             NaN             NaN   

        action_taken_6  is_blackjack_dealer  is_blackjack_player  
236016             NaN                    0                    0  
105365             NaN                    0                    0  
89383              NaN                    0                    0  
145073             NaN                    0                    0  
207067             NaN                    0                    0  

[5 rows x 34 columns]

# Analysis

We will now analyse our dataset to get some statistics about the game.

In [22]:
data['win'].value_counts()

-1    124301
 1    110576
 0     22127
Name: win, dtype: int64

In [23]:
data['win'].value_counts(normalize=True)

-1    0.483654
 1    0.430250
 0    0.086096
Name: win, dtype: float64

We might think that our classification from before is incorrect, as from the distribution it looks like there is class bias. However, by looking for theoretical black jack probabilities, we can see that they are very close to the values we got, so our classification is correct!

More about blackjack probabilities: [here](https://www.onlinegambling.com/blackjack/odds/#:~:text=23%25-,Odds%20of%20Winning%20Blackjack,of%20a%20loss%20at%2049.10%25.)

In [24]:
sum(data['win'])

-13725

The odds arent really for player's favor...

In [25]:
data['dealer_up'].value_counts()

10    77355
6     20483
5     20441
2     20238
4     20186
3     20024
7     19963
8     19786
9     19400
11    19128
Name: dealer_up, dtype: int64

As expected 10 appears almost 4x more than other cards , since 10 is represented by 4 cards - 10,J,Q,K. Excluding that the cards are balanced.

In [26]:
sum(data['is_blackjack_dealer']) / len(data['dealer_final_value']) , sum(data['is_blackjack_player']) / len(data['player_final_value'])

(0.04602262999797668, 0.046248307419339774)

We can see approximately 4.6% of the hands ended in blackjack for either player or dealer, [corresponding to theorey](https://betandbeat.com/blackjack/blog/odds-of-getting-blackjack/#:~:text=It%20is%20simpler%20to%20calculate,the%20player%20are%20about%204.8%25.).

In [27]:
data['actions_taken'].astype(str).value_counts().head(20)

['S']                   104799
['H', 'S']               34806
['D']                    24463
['H']                    16680
['H', 'H', 'S']          12640
['R']                    10306
['H', 'H']               10078
['N']                     5938
[]                        5890
['P', 'S']                5137
['N', 'S']                3551
['P']                     2701
['N', 'R']                2567
['N', 'H', 'S']           2448
['H', 'H', 'H']           2442
['P', 'D']                2092
['H', 'H', 'H', 'S']      2067
['P', 'H', 'S']           1410
['N', 'H']                1228
['N', 'H', 'H', 'S']      1112
Name: actions_taken, dtype: int64

The empty brackets [] seem suspicious. There are no null objects so one possible option is blackjack at first, as if that is the case the player has no action to do and the round is automatically over. We'll make sure that is the case.

In [28]:
data[['dealer_up','win']].groupby('dealer_up')['win'].mean().sort_values(ascending=False)

dealer_up
6     0.147537
5     0.114525
7     0.094825
4     0.090261
3     0.059928
2     0.035824
8    -0.005054
9    -0.077165
10   -0.200129
11   -0.399937
Name: win, dtype: float64

In [29]:
data['initial_hand'] = data['initial_hand'].astype(str)
data[['initial_hand','win']].groupby('initial_hand')['win'].mean().sort_values(ascending=False)

initial_hand
[11, 10]    0.874769
[10, 11]    0.871489
[11, 9]     0.574612
[10, 10]    0.572164
[9, 11]     0.563930
              ...   
[10, 6]    -0.413236
[7, 8]     -0.430194
[6, 9]     -0.434309
[7, 9]     -0.451440
[9, 7]     -0.461222
Name: win, Length: 100, dtype: float64

In [30]:
data['initial_hand'] = data['initial_hand'].astype(str)
data[['initial_hand','win']].groupby('initial_hand')['win'].value_counts().head(25)

initial_hand  win
[10, 10]       1     16511
               0      4243
              -1      2949
[10, 11]       1      5181
               0       764
[10, 2]       -1      3739
               1      1926
               0       288
[10, 3]       -1      3920
               1      1903
               0       233
[10, 4]       -1      3957
               1      1696
               0       253
[10, 5]       -1      4257
               1      1755
               0        85
[10, 6]       -1      4122
               1      1693
               0        63
[10, 7]       -1      3369
               1      1610
               0       816
[10, 8]       -1      2668
               1      2500
Name: win, dtype: int64

# Graphs

Now for a few graphs for the analysis.

We first start with a function to set 11 to 1 for hands with sum above 21, this will be helpful later:

In [31]:
def hands_normalizer(data,maxhandsnum):
        for i in range(1,maxhandsnum+1):
            if i == 1:
                data.loc[(data.loc[:,'cards_sum'] > 21) & ((data.loc[:,f'player_card_{i}'] == 11) | (data.loc[:,f'player_card_{i+1}'] == 11)) ,'cards_sum']  -= 10
                continue
            elif i == 2:
                continue
            else:
                data.loc[(data.loc[:,'cards_sum'] > 21) & (data.loc[:,f'player_card_{i}'] == 11) ,'cards_sum']  -= 10

We first want to check what step should we take at a certain point. We will map all steps for each sum of cards we have and each dealer card that gives us the biggest probability of winning.

In [32]:
def step_graph_generator(data,step):
    columns = ['dealer_up','win']
    hands = []
    for i in range(1,step+2):
        hands.append(f'player_card_{i}')
    columns = columns + [f'action_taken_{step}'] + hands
    graphdata = data[columns]
    graphdata['cards_sum'] = graphdata['player_card_1'] 
    for i in range(2,step+2):
        graphdata.loc[:,'cards_sum'] += graphdata.loc[:,f'player_card_{i}'] 
    hands_normalizer(graphdata,step+1)
    Graph = graphdata.query('win == 1')
    Graph['Counts'] = Graph.groupby(['cards_sum','dealer_up'])[f'action_taken_{step}'].transform('count')
    MaxIndex = Graph.groupby(['cards_sum','dealer_up'])['Counts'].idxmax().drop_duplicates()
    FinalGraph = Graph.loc[MaxIndex,:].sort_values(['cards_sum','dealer_up']).fillna('No Data')
    FinalGraph = FinalGraph.replace({ 'S' : 'Stand', 'H' : 'Hit' , 'D' : 'Double' , 'P' : 'Split' , 'R' : 'Surrender' , 'N' : 'No Insurance'})
    return px.scatter(FinalGraph, x='cards_sum', y='dealer_up', color=f'action_taken_{step}' , hover_data=[f'action_taken_{step}'] , labels={
                     'cards_sum': 'Player\'s Cards Sum', 'dealer_up': 'Dealer\'s Card Up', f'action_taken_{step}': 'Action'} ,
                      color_discrete_map={ 'Stand': '#FC2020', 'Hit': '#09D138' , 'Double': "#009999", 'Split': '#FF3399', 'Surrender': "#CCCC00", 'No Insurance': "#B266FF", 'No Data': '#C0C0C0'}, 
                      title=f'Step {step}').update_traces(marker=dict(size=15,line=dict(width=1,color='DarkSlateGrey')))

@widgets.interact
def show_action_graphs(step=widgets.IntSlider(value=1, min=1, max=6, step=1)):
    return step_graph_generator(data,step)

interactive(children=(IntSlider(value=1, description='step', max=6, min=1), Output()), _dom_classes=('widget-i…

Now we will also map all actions not as most recommended but as histogram:

In [33]:
def step_bar_graph_generator(data,step):
    columns = ['dealer_up','win']
    hands = []
    for i in range(1,step+2):
        hands.append(f'player_card_{i}')
    columns = columns + [f'action_taken_{step}'] + hands
    graphdata = data[columns]
    graphdata['cards_sum'] = graphdata['player_card_1'] 
    for i in range(2,step+2):
        graphdata.loc[:,'cards_sum'] += graphdata.loc[:,f'player_card_{i}'] 
    hands_normalizer(graphdata,step+1)
    Graph = graphdata.query('win == 1')
    Graph['Counts'] = Graph.groupby(['cards_sum','dealer_up'])[f'action_taken_{step}'].transform('count')
    MaxIndex = Graph.groupby(['cards_sum','dealer_up'])['Counts'].idxmax().drop_duplicates()
    FinalGraph = Graph.loc[MaxIndex,:].sort_values(['cards_sum','dealer_up']).fillna('No Data')
    FinalGraph = FinalGraph.replace({ 'S' : 'Stand', 'H' : 'Hit' , 'D' : 'Double' , 'P' : 'Split' , 'R' : 'Surrender' , 'N' : 'No Insurance'})
    return px.histogram(FinalGraph, x='cards_sum', color=f'action_taken_{step}' , hover_data=[f'action_taken_{step}'] , labels={
                     'cards_sum': 'Player\'s Cards Sum', f'action_taken_{step}': 'Action'} ,
                      color_discrete_map={ 'Stand': '#FC2020', 'Hit': '#09D138' , 'Double': "#009999", 'Split': '#FF3399', 'Surrender': "#CCCC00", 'No Insurance': "#B266FF", 'No Data': '#C0C0C0'}, 
                      title=f'Step {step}')

@widgets.interact
def show_bar_graphs(step=widgets.IntSlider(value=1, min=1, max=6, step=1)):
    return step_bar_graph_generator(data,step)

interactive(children=(IntSlider(value=1, description='step', max=6, min=1), Output()), _dom_classes=('widget-i…

Recommended action per first 2 cards and dealer's up card:

In [34]:
StepBy1stHand = data[['initial_hand','dealer_up','win','action_taken_1']]
StepBy1stHand['initial_hand'] = StepBy1stHand['initial_hand'].astype(str)
GraphD = StepBy1stHand.query('win == 1')
GraphD['Counts'] = GraphD.groupby(['initial_hand','dealer_up'])['action_taken_1'].transform('count')
MaxIndexD = GraphD.groupby(['initial_hand','dealer_up'])['Counts'].idxmax().drop_duplicates()
NewGraphD = GraphD.loc[MaxIndexD,:].sort_values(['initial_hand','dealer_up']).fillna('No Data')
NewGraphD = NewGraphD.replace({ 'S' : 'Stand', 'H' : 'Hit' , 'D' : 'Double' , 'P' : 'Split' , 'R' : 'Surrender' , 'N' : 'No Insurance'})
px.scatter(NewGraphD, x='initial_hand', y='dealer_up', color='action_taken_1', hover_data=['action_taken_1'] , labels={
                     'initial_hand': 'Player\'s Hand', 'dealer_up': 'Dealer\'s Card Up', 'action_taken_1': 'Action'} ,
                      color_discrete_map={ 'Stand': '#FC2020', 'Hit': '#09D138' , 'Double': "#009999", 'Split': '#FF3399', 'Surrender': "#CCCC00", 'No Insurance': "#B266FF", 'No Data': '#C0C0C0'}, 
                      title='Step 1 by first cards').update_traces(marker=dict(size=10,line=dict(width=1,color='DarkSlateGrey')))


And the matching histogram:

In [35]:
StepBy1stHand = data[['initial_hand','dealer_up','win','action_taken_1']]
StepBy1stHand['initial_hand'] = StepBy1stHand['initial_hand'].astype(str)
GraphD = StepBy1stHand.query('win == 1')
GraphD['Counts'] = GraphD.groupby(['initial_hand','dealer_up'])['action_taken_1'].transform('count')
MaxIndexD = GraphD.groupby(['initial_hand','dealer_up'])['Counts'].idxmax().drop_duplicates()
NewGraphD = GraphD.loc[MaxIndexD,:].sort_values(['initial_hand','dealer_up']).fillna('No Data')
NewGraphD = NewGraphD.replace({ 'S' : 'Stand', 'H' : 'Hit' , 'D' : 'Double' , 'P' : 'Split' , 'R' : 'Surrender' , 'N' : 'No Insurance'})
px.histogram(NewGraphD, x='initial_hand', color='action_taken_1', hover_data=['action_taken_1'] , labels={
                     'initial_hand': 'Player\'s Hand', 'dealer_up': 'Dealer\'s Card Up', 'action_taken_1': 'Action'} ,
                      color_discrete_map={ 'Stand': '#FC2020', 'Hit': '#09D138' , 'Double': "#009999", 'Split': '#FF3399', 'Surrender': "#CCCC00", 'No Insurance': "#B266FF", 'No Data': '#C0C0C0'}, 
                      title='Step 1 by first cards')

Now we will try mapping the round results per the actions taken and sum of cards of the player/dealer:

In [36]:
def win_by_action_graph_generator(data,step ,norm):
    graphdata = data[[f'action_taken_{step}','win']]
    graphdata = graphdata.replace({ 'S' : 'Stand', 'H' : 'Hit' , 'D' : 'Double' , 'P' : 'Split' , 'R' : 'Surrender' , 'N' : 'No Insurance' ,  1 : 'Win', 0 : 'Push' ,-1 : 'Loss'})
    if norm == False:
        return px.histogram(graphdata, x=f'action_taken_{step}', color='win' , hover_data=['win'] , text_auto=True , labels={
                      f'action_taken_{step}': 'Action'} , color_discrete_map={ 'Loss': '#FC2020', 'Win': '#09D138' , 'Push': "#009999"},  
                      title=f'Step {step}')
    elif norm == True:
        return px.histogram(graphdata, x=f'action_taken_{step}', color='win' , hover_data=['win'] , text_auto=True , barnorm = 'percent' , labels={
                      f'action_taken_{step}': 'Action'} , color_discrete_map={ 'Loss': '#FC2020', 'Win': '#09D138' , 'Push': "#009999"},  
                      title=f'Step {step}')

@widgets.interact
def show_win_by_action_graphs(step=widgets.IntSlider(value=1, min=1, max=6, step=1) , norm = widgets.ToggleButtons( options=[True,False] , value=False , description='Normalized')):
    return win_by_action_graph_generator(data,step , norm)

interactive(children=(IntSlider(value=1, description='step', max=6, min=1), ToggleButtons(description='Normali…

Whats interesting is that we can see that almost sweepingly standing gives us the best win chances, regardless of the hand!

We will create another graph to try to support this claim, we will plot the mean win as player's amount of cards:


In [37]:
WinMean = pd.DataFrame(data['win'])
WinMean['len'] = data['player_final'].apply(lambda x: len(x))
WinMeanPlotData = pd.DataFrame(WinMean.groupby(['len'])['win'].mean())
px.scatter(WinMeanPlotData , x=WinMeanPlotData.index , y='win' , hover_data=['win'] , labels={
                     'len': 'Amount of player\'s cards holding', 'win' : 'Mean Win'}).update_traces(marker=dict(size=12,line=dict(width=1,color='DarkSlateGrey')))

This also supports our claim. The graph is monotonically decreasing.

Notice that when holding only 2 cards (meaning standing after getting the first 2 cards and immediately standing) the mean is **positive**!

Now we'll plot win distribution per sum of cards and current step:

In [38]:
def win_graph_generator(data,step):
    hands = []
    for i in range(1,step+2):
        hands.append(f'player_card_{i}')
    columns = hands + ['win']
    graphdata = data[columns]
    graphdata['cards_sum'] = graphdata['player_card_1'] 
    for i in range(2,step+2):
        graphdata.loc[:,'cards_sum'] += graphdata.loc[:,f'player_card_{i}'] 
    hands_normalizer(graphdata,step+1)
    graphdata = graphdata.replace({ 1 : 'Win', 0 : 'Push' ,-1 : 'Loss'})
    return px.histogram(graphdata, x='cards_sum', color='win' , hover_data=['win'] , text_auto=True , labels={
                     'cards_sum': 'Player\'s Cards Sum', 'count' : 'Counts'} ,
                      color_discrete_map={ 'Loss': '#FC2020', 'Win': '#09D138' , 'Push': "#009999"}, 
                      title=f'Step {step}')

@widgets.interact
def win_bar_graphs(step=widgets.IntSlider(value=1, min=1, max=6, step=1)):
    return win_graph_generator(data,step)

interactive(children=(IntSlider(value=1, description='step', max=6, min=1), Output()), _dom_classes=('widget-i…

Not suprisingly , we can see that when the players sum is 21, regardless of the step, it either won or had a push (as it cant lose), and once the sum is above 22 it always lost therefore entirely red in our chart.

In [39]:
def win_total_graph_generator(data,selection,norm):
    if selection == 'dealer':
        graphdata = data[['dealer_final_value','win']].replace({ -1 : 'Win', 0 : 'Push' ,1 : 'Loss'})  # Normalizing win for dealer
    elif selection == 'player':
        graphdata = data[['player_final_value','win']].replace({ 1 : 'Win' , 0 : 'Push' ,-1 : 'Loss'})
    if norm == False:
        return px.histogram(graphdata, x=f'{selection}_final_value', color='win' , hover_data=['win'] , labels={
                     f'{selection}_final_value': f'{selection}\'s Cards Sum', 'count' : 'Counts'} , text_auto=True ,
                      color_discrete_map={ 'Loss': '#FC2020', 'Win': '#09D138' , 'Push': "#009999"}, 
                      title=(f'{selection}\'s distribution per sum of cards'))
    if norm == True:
        return px.histogram(graphdata, x=f'{selection}_final_value', color='win' , hover_data=['win'] , barnorm = 'percent' , labels={
                     f'{selection}_final_value': f'{selection}\'s Cards Sum', 'count' : 'Counts'} , text_auto=True ,
                      color_discrete_map={ 'Loss': '#FC2020', 'Win': '#09D138' , 'Push': "#009999"}, 
                      title=(f'{selection}\'s distribution per sum of cards'))
    
@widgets.interact
def win_total_bar_graphs(selection= widgets.ToggleButtons( options=['player', 'dealer'] , value='player' , description='Selection') , norm = widgets.ToggleButtons( options=[True,False] , value=False , description='Normalized')):
    return win_total_graph_generator(data,selection,norm)

interactive(children=(ToggleButtons(description='Selection', options=('player', 'dealer'), value='player'), To…

Keep in mind the win refers to the side youre viewing (i.e - win in dealer's graph means the dealer **won** and player **lost**)

We might notice a strange behavior when the dealer's sum of cards is over 21. The colors are partially green which means the dealer won with a sum of cards of above 21 and did not bust. If we recall, the dealer is the last to play, so if the player busted, the dealer wins regardless his sum of cards. We can also see the minimum value in the chart is 17 which makes sense as the dealer must play until it reaches a minimum sum of 17.

Simplified box plot of win per dealer/player final value.

In [40]:
def win_box_plot_generator(data,side):
    if side == 'dealer':
        return px.box(data.replace({ 1 : 'Loss', 0 : 'Push' ,-1 : 'Win'}), x='win', y='dealer_final_value' , color='win' ,
                      color_discrete_map={ 'Loss': '#FC2020', 'Win': '#09D138' , 'Push': "#009999"}, 
                      title=f'Win distribution')
    elif side == 'player':
        return px.box(data.replace({ 1 : 'Win', 0 : 'Push' ,-1 : 'Loss'}), x='win', y='player_final_value' , color='win' ,
                      color_discrete_map={ 'Loss': '#FC2020', 'Win': '#09D138' , 'Push': "#009999"}, 
                      title=f'Win distribution')

@widgets.interact
def show_win_box_plot(side = widgets.ToggleButtons( options=['player','dealer'] , value='player' , description='side')):
    return win_box_plot_generator(data,side)

interactive(children=(ToggleButtons(description='side', options=('player', 'dealer'), value='player'), Output(…

Keep in mind the win refers to the side youre viewing (i.e - win in dealer's graph means the dealer **won** and player **lost**)

After the statistical extraction and comparasion to the theoretical statistics and probabilities, we can see our data corresponds to it. We can proceed to build our required models.

# Modeling

We will now create a model to try to predict results of a blackjack hands given the data we have.

In [41]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

We first start with correlation matrix to see if there is any correlation in our data

In [42]:
corrmatx = data.corr()
corrmatx

shoe_id  cards_remaining  dealer_up  dealer_final_value  \
shoe_id              1.000000        -0.000532   0.003024           -0.000552   
cards_remaining     -0.000532         1.000000  -0.000765            0.000735   
dealer_up            0.003024        -0.000765   1.000000           -0.088629   
dealer_final_value  -0.000552         0.000735  -0.088629            1.000000   
player_final_value   0.001173         0.000677   0.274481           -0.088044   
run_count            0.008095        -0.007900   0.041839            0.009955   
true_count           0.000697        -0.016245   0.044593            0.009621   
win                 -0.001753        -0.000644  -0.137173            0.324960   
player_card_1       -0.002200        -0.000178   0.005275           -0.001336   
player_card_2       -0.000121        -0.001594  -0.011639           -0.001241   
player_card_3       -0.003488         0.001224  -0.007598           -0.004434   
player_card_4        0.001072         0.008169  -0.004724           -0.001091   
player_card_5        0.010449        -0.021061  -0.027585            0.000371   
player_card_6        0.019784         0.005053  -0.016072           -0.008674   
player_card_7        0.102090         0.095636   0.104636           -0.112904   
dealer_card_1        0.003024        -0.000765   1.000000           -0.088629   
dealer_card_2       -0.001385        -0.002583   0.000279           -0.083188   
dealer_card_3        0.002260         0.000305   0.001017            0.264756   
dealer_card_4        0.003155         0.007582   0.003231            0.467193   
dealer_card_5        0.003523        -0.012652  -0.004505            0.596769   
dealer_card_6       -0.051417        -0.046477   0.012301            0.619310   
dealer_card_7        0.029398         0.081583  -0.107554            0.696718   
is_blackjack_dealer  0.001342        -0.004268   0.244557            0.055031   
is_blackjack_player -0.001818        -0.001534   0.003597           -0.000310   

                     player_final_value  run_count  true_count       win  \
shoe_id                        0.001173   0.008095    0.000697 -0.001753   
cards_remaining                0.000677  -0.007900   -0.016245 -0.000644   
dealer_up                      0.274481   0.041839    0.044593 -0.137173   
dealer_final_value            -0.088044   0.009955    0.009621  0.324960   
player_final_value             1.000000   0.028943    0.029591  0.082590   
run_count                      0.028943   1.000000    0.860525  0.011044   
true_count                     0.029591   0.860525    1.000000  0.013081   
win                            0.082590   0.011044    0.013081  1.000000   
player_card_1                  0.113636   0.043596    0.046402  0.146716   
player_card_2                  0.107844   0.038383    0.041620  0.144276   
player_card_3                  0.252793   0.043342    0.045681 -0.032032   
player_card_4                  0.417970   0.048026    0.047766 -0.235404   
player_card_5                  0.547386   0.032740    0.029274 -0.367752   
player_card_6                  0.575889   0.012237    0.016990 -0.493357   
player_card_7                  0.585452  -0.099470   -0.039987 -0.631408   
dealer_card_1                  0.274481   0.041839    0.044593 -0.137173   
dealer_card_2                 -0.074390   0.040499    0.043983 -0.089730   
dealer_card_3                  0.001044   0.042959    0.045611  0.115912   
dealer_card_4                  0.001878   0.041624    0.043193  0.271068   
dealer_card_5                  0.006252   0.047274    0.042044  0.381795   
dealer_card_6                 -0.000876   0.032345    0.061674  0.447380   
dealer_card_7                 -0.089611   0.028573   -0.091415  0.354751   
is_blackjack_dealer           -0.240310   0.020737    0.023203 -0.206756   
is_blackjack_player            0.187414   0.022141    0.024666  0.213756   

                     player_card_1  player_card_2  ...  player_card_7  \
shoe_id               

From a brief look we can see there are no correlating values, but since its a large dataset its better to visualize it.

In [43]:
px.imshow(corrmatx)

Almost no correlation, except trivial pairs such as run_count-true_count or dealer_card_1 - dealer_up , which will be corrected. Also some of the pixels are N/A due to lack of information, will also be corrected.

In [44]:
from sklearn.model_selection import train_test_split
from sklearn import tree
from sklearn import metrics
from sklearn.metrics import classification_report

Preprocessing the data before modeling:

In [45]:
prepdata = data.sample(n=30000)  

We chose n=30000 due to computational time. In general you can choose whatever value you want.

We will now remove a lot of data from this table. The removed data is one of 2 categories:

-**Duplicate data**: Data that exists in 2 or more columns in any form

**-Non relevant data**: Data that is not relevant to the solution

In [46]:
prepdata.drop(['dealer_up','initial_hand','dealer_final','dealer_final_value','player_final','player_final_value','actions_taken'],axis=1,inplace=True)  # Duplicate data
prepdata.drop(['shoe_id'],axis=1,inplace=True) # Not relevant

As said beforem the shoe_id is not relevant , neither are the actions_taken, 

Now we will try to get our wanted data prepared for modeling.

In [47]:
prepdata.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 30000 entries, 183657 to 149270
Data columns (total 26 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   cards_remaining      30000 non-null  int64  
 1   run_count            30000 non-null  int64  
 2   true_count           30000 non-null  int64  
 3   win                  30000 non-null  int64  
 4   player_card_1        30000 non-null  int64  
 5   player_card_2        30000 non-null  int64  
 6   player_card_3        13651 non-null  float64
 7   player_card_4        3701 non-null   float64
 8   player_card_5        669 non-null    float64
 9   player_card_6        71 non-null     float64
 10  player_card_7        7 non-null      float64
 11  dealer_card_1        30000 non-null  int64  
 12  dealer_card_2        30000 non-null  int64  
 13  dealer_card_3        20033 non-null  float64
 14  dealer_card_4        6707 non-null   float64
 15  dealer_card_5        1257 non-

We can see player and dealer cards columns contains NaNs. Since cards are categorial data, we can fill all NaNs with -1 for example. We can also see some columns are of float type and not int, which is not acceptable by the KNN. We will turn the values to integers for the KNN as all our values are singular

In [48]:
prepdata[['action_taken_1','action_taken_2','action_taken_3','action_taken_4','action_taken_5','action_taken_6']] = prepdata[['action_taken_1','action_taken_2','action_taken_3','action_taken_4','action_taken_5','action_taken_6']].replace({ 'S' : 1, 'H' : 2 , 'D' : 3 , 'P' : 4 , 'R' : 5 , 'N' : 6})

In [49]:
prepdata = prepdata.fillna(0).astype('int')
prepdata.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 30000 entries, 183657 to 149270
Data columns (total 26 columns):
 #   Column               Non-Null Count  Dtype
---  ------               --------------  -----
 0   cards_remaining      30000 non-null  int64
 1   run_count            30000 non-null  int64
 2   true_count           30000 non-null  int64
 3   win                  30000 non-null  int64
 4   player_card_1        30000 non-null  int64
 5   player_card_2        30000 non-null  int64
 6   player_card_3        30000 non-null  int64
 7   player_card_4        30000 non-null  int64
 8   player_card_5        30000 non-null  int64
 9   player_card_6        30000 non-null  int64
 10  player_card_7        30000 non-null  int64
 11  dealer_card_1        30000 non-null  int64
 12  dealer_card_2        30000 non-null  int64
 13  dealer_card_3        30000 non-null  int64
 14  dealer_card_4        30000 non-null  int64
 15  dealer_card_5        30000 non-null  int64
 16  dealer_card_6   

Now lets see our correlation matrix after all processing:

In [50]:
px.imshow(prepdata.corr())

In [51]:
prepdata['win'].value_counts()

-1    14462
 1    12889
 0     2649
Name: win, dtype: int64

The sample data is also (unsuprisingly) unbalanced in the same proportions as the mother-data. We must consider that in some models that can not handle unbalanced data.

And now our data is ready for modeling!

For the modeling, we will weigh mostly on percision for scoring, as we want the least false classifications (we dont want to donate any money to the casino..) 

## KNN

The first model we will start with is KNN , since its the simplest classification model and handles unbalanced data quite well. We will run this model for several hyper parameters (k) to look for the best performing model.

In [52]:
from sklearn.neighbors import KNeighborsClassifier

In [53]:
KNNlist = [x for x in range(1,26,2)]
acclist = []
perlist = []
conflist = {}
x_train,x_test,y_train,y_test= train_test_split(prepdata.drop('win',axis=1),prepdata['win'], test_size=0.2,random_state=42)
for k in KNNlist:
    knnfittype = KNeighborsClassifier(n_neighbors=k)
    knnfittype.fit(x_train,y_train)
    y_pred = knnfittype.predict(x_test)
    accuracy = metrics.accuracy_score(y_test,y_pred)
    percision =  metrics.precision_score(y_test,y_pred,average='weighted')
    confmatx = pd.DataFrame({'True':y_test, 'Predicted': y_pred}).groupby(['True','Predicted']).size()
    acclist.append(accuracy)
    perlist.append(percision)
    conflist[k] = confmatx
totalscore = pd.DataFrame({'Accuracy' : acclist , 'Percision' : perlist} , index = KNNlist)
totalscore

Accuracy  Percision
1   0.580667   0.581586
3   0.605333   0.582736
5   0.605000   0.584118
7   0.611333   0.584482
9   0.617333   0.588453
11  0.615500   0.585601
13  0.620500   0.587877
15  0.622667   0.591382
17  0.624500   0.595760
19  0.627500   0.595543
21  0.624833   0.592866
23  0.623667   0.592472
25  0.622833   0.589865

In [54]:
def knn_confusin_matrix(conflist,step):
    return print(conflist.get(step))

@widgets.interact
def knn_confusin_matrix_widg(step=widgets.IntSlider(value=1, min=1, max=26, step=2 , description='K Value')):
    return knn_confusin_matrix(conflist,step)

interactive(children=(IntSlider(value=1, description='K Value', max=26, min=1, step=2), Output()), _dom_classe…

In [55]:
accperfig = make_subplots(rows=2, cols=1 , subplot_titles=("Accuracy vs k for KNN model", "Accuracy vs k for KNN model"))

# Add traces
accperfig.add_trace(go.Scatter(x=totalscore.reset_index()['index'], y= totalscore.reset_index()['Accuracy'],
                    mode='markers',
                    name='Accuracy') ,  row=1, col=1).update_traces(marker=dict(size=12,line=dict(width=1,color='DarkSlateGrey')))

accperfig.add_trace(go.Scatter(x=totalscore.reset_index()['index'], y= totalscore.reset_index()['Percision'],
                    mode='markers',
                    name='Percision') ,  row=2, col=1).update_traces(marker=dict(size=12,line=dict(width=1,color='DarkSlateGrey')))

accperfig.update_layout(height=800, width=900, title_text="Accuracy & Percision for KNN model")
accperfig.show()

We did not get good accuracy/percision, for any hyper parameter. Perhaps one of the reason is the very high dimension of the model.There are 24 columns to fit therefor the dimension is 24, which might make it difficult to fit the data. Another thing we can notice is that while the model is classifying the 'Win' and 'Loss' hands better as k is bigger, its struggling to fit the Push hands. 

k varies heavily on the randomly chosen data therefore we can not conclude what k is the best for our model (For each run we get different k value with the best accuracy and percision)

## Random Forest

The next method we'll choose is *Random Forest*. We'll choose this method as its simple and easy for discrete and low-ranged data like this. Unlike the KNN, it does not handle unbalanced data quite well, however scikit-learn has a function to tackle those kind of situations, so we'll use it when fitting.

In [56]:
from sklearn.ensemble import RandomForestClassifier

In [57]:
x_train,x_test,y_train,y_test= train_test_split(prepdata.drop('win',axis=1),prepdata['win'],test_size=0.2,random_state=42)
rffittype = RandomForestClassifier(class_weight= 'balanced')
rffittype.fit(x_train,y_train)
y_pred = rffittype.predict(x_test)
print(classification_report(y_test, y_pred , digits = 3))

              precision    recall  f1-score   support

          -1      0.867     0.888     0.877      2833
           0      0.775     0.301     0.433       539
           1      0.823     0.905     0.862      2628

    accuracy                          0.843      6000
   macro avg      0.822     0.698     0.724      6000
weighted avg      0.839     0.843     0.831      6000



In [58]:
pd.DataFrame({'True':y_test, 'Predicted': y_pred}).groupby(['True','Predicted']).size()

True  Predicted
-1    -1           2515
       0             21
       1            297
 0    -1            163
       0            162
       1            214
 1    -1            224
       0             26
       1           2378
dtype: int64

We can see we got good percision relatively ( ~ 84%) and F1 score (~ 83%).As said its perhaps because our data is relatively easy to fit for decision trees.

We will also take advantage of this method to check for the importance of our parameters:

In [59]:
importance = rffittype.feature_importances_
params = prepdata.drop('win',axis=1).columns
importancetable = pd.DataFrame({'Parameter' : params , 'Importance' : importance})
px.bar(importancetable, x='Parameter', y='Importance')

As expected, the parameters with the least occurences (cards and actions that were pulled after a lot of cards before) had the least importance contribution. However we can not ignore then as they are still a part of a hand and we will lose important info. Besides then almost all other params had more or less equal contribution.

## Gradient Boosting

We would also test the *Gradient Boosting* model, as its also a form of decision tree and usually outperforms the Random Forest method. It is usually used when there is concern of high bias (overfit) in regular decision tree, which *might* be our case (since our data is very simple and can fall into the overfit territory). The problem with this method that as it also handles unbalanced data quite bad, it does not have an easy and explicit solution like the Random Forest, so we will have to tackle this issue already in the test train split. 

In [60]:
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import StratifiedShuffleSplit

In [61]:
x_train,x_test,y_train,y_test= train_test_split(prepdata.drop('win',axis=1),prepdata['win'],test_size=0.2,random_state=42)
gbfittype = GradientBoostingClassifier()
gbfittype.fit(x_train,y_train)
y_pred = gbfittype.predict(x_test)
print(classification_report(y_test, y_pred, digits = 3))

              precision    recall  f1-score   support

          -1      0.790     0.856     0.822      2833
           0      0.810     0.032     0.061       539
           1      0.764     0.846     0.803      2628

    accuracy                          0.778      6000
   macro avg      0.788     0.578     0.562      6000
weighted avg      0.781     0.778     0.745      6000



In [62]:
pd.DataFrame({'True':y_test, 'Predicted': y_pred}).groupby(['True','Predicted']).size()

True  Predicted
-1    -1           2425
       0              2
       1            406
 0    -1            241
       0             17
       1            281
 1    -1            402
       0              2
       1           2224
dtype: int64

However, inspite of the good accuracy and percision relatively, we can see it did not perform Random Forest in our case! It mostly fails to classify the 'Push' situations.

**Logistic Regression**

Once last method we will try is *Logistic Regression*. It is intuitively the best method to chose as we are fitting Win-Loss situations, however the addition of Push situation makes it a bit more complex. Therefore we would fit it in the *One vs. Rest* method

In [63]:
from sklearn.linear_model import LogisticRegression

In [64]:
x_train,x_test,y_train,y_test= train_test_split(prepdata.drop('win',axis=1),prepdata['win'],test_size=0.2,random_state=42)
logfittype = LogisticRegression(multi_class='ovr', solver='liblinear' , class_weight= 'balanced')
logfittype.fit(x_train,y_train)
y_pred = logfittype.predict(x_test)
print(classification_report(y_test, y_pred, digits = 3))
accuracy = metrics.accuracy_score(y_test,y_pred)
percision =  metrics.precision_score(y_test,y_pred,average='weighted')
pd.DataFrame({'True':y_test, 'Predicted': y_pred}).groupby(['True','Predicted']).size()

              precision    recall  f1-score   support

          -1      0.682     0.652     0.667      2833
           0      0.239     0.362     0.288       539
           1      0.649     0.611     0.630      2628

    accuracy                          0.608      6000
   macro avg      0.523     0.542     0.528      6000
weighted avg      0.628     0.608     0.616      6000



True  Predicted
-1    -1           1848
       0            266
       1            719
 0    -1            195
       0            195
       1            149
 1    -1            667
       0            355
       1           1606
dtype: int64

Unlike our intuition, the model does not perform quite well. Perhaps because the linear correlation between the parameters is not so strong. Once again we see there was a problem classifying the Push situations.

# Summary

In this notebook, we managed to develop a model with ~85% percision that predicts results of a blackjack hand. We also showed statistically proven situations where the odds can be tilted to the player's favor and what action should be taken at each step to increase the odds of winning.

The notebook can be further developed to a further statistical evaluation of the game, cards counting and model improving.